In [1]:
from datetime import date
import numpy as np
import pandas as pd
import datetime
import sys
from yahoo_finance_api2 import share
from yahoo_finance_api2.exceptions import YahooFinanceError

In [2]:
import plotly
plotly.__version__

from datetime import date
import yahoo_finance as yf

In [3]:
import cufflinks as cf
import plotly.offline
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

In [4]:
# (*) Graph objects to piece together plots
import plotly.graph_objs as go

In [5]:
def fetch_data(ticker_list, verbose=True):
    stock_list = []
    for tick in ticker_list:
        if verbose:
            print(f"Fetching ticker: {tick}...")
        my_share = None
        my_share = share.Share(tick)
        symbol_data = None
        try:
            symbol_data = my_share.get_historical(share.PERIOD_TYPE_YEAR,7,
                                                  share.FREQUENCY_TYPE_DAY,1)
        except YahooFinanceError as e:
            print(e.message)
            sys.exit(1)

        stock_list.append(symbol_data)
        if verbose:
            print(f"Len of timestamp series: {len(symbol_data['timestamp'])}")
    return stock_list

def datetime_from_timestamp(timestamp):
    x = datetime.date.fromtimestamp(int(str(timestamp)[:-3]))
    return pd.to_datetime(
        f"{str(x.year)}-{str(x.month)}-{str(x.day)}")

In [6]:
ticker_list=['BARN.SW',
             'E5H.SI',
             'BN.VI', # DANONE
             'UN', # unilever
             'LISN.SW', #lind
             'SJM', #JM SMUCKER 
             'MDLZ', # mondelez
             'HRL', # Hormel foods
             'GIS', # GENERAL MILLS
             'HSY',
             'KIKOY',
             'WHG',
             'ADM',
             'K',
             'NESN.SW',
             'TATE.L',
             'BG',
             'ABF.L',
             'CAG'
             ]

data = fetch_data(ticker_list)

Fetching ticker: BARN.SW...
Len of timestamp series: 1753
Fetching ticker: E5H.SI...
Len of timestamp series: 1758
Fetching ticker: BN.VI...
Len of timestamp series: 1741
Fetching ticker: UN...
Len of timestamp series: 1761
Fetching ticker: LISN.SW...
Len of timestamp series: 1753
Fetching ticker: SJM...
Len of timestamp series: 1761
Fetching ticker: MDLZ...
Len of timestamp series: 1761
Fetching ticker: HRL...
Len of timestamp series: 1761
Fetching ticker: GIS...
Len of timestamp series: 1761
Fetching ticker: HSY...
Len of timestamp series: 1761
Fetching ticker: KIKOY...
Len of timestamp series: 1761
Fetching ticker: WHG...
Len of timestamp series: 1761
Fetching ticker: ADM...
Len of timestamp series: 1761
Fetching ticker: K...
Len of timestamp series: 1761
Fetching ticker: NESN.SW...
Len of timestamp series: 1753
Fetching ticker: TATE.L...
Len of timestamp series: 1770
Fetching ticker: BG...
Len of timestamp series: 1761
Fetching ticker: ABF.L...
Len of timestamp series: 1770
Fetchin

In [7]:
def get_pandas_df(data):
    min_series = []
    # Take the first as base df
    stocks = pd.DataFrame()
    stocks['timestamp'] = list(map(datetime_from_timestamp, data[0]['timestamp']))
    stocks[f'{ticker_list[0]}_close'] = data[0]['close']
    for idx, stock in enumerate(data):
        if idx!=0:
            temp_df = pd.DataFrame()
            temp_df['timestamp'] = list(map(datetime_from_timestamp, stock['timestamp']))
            temp_df[f'{ticker_list[idx]}_close'] = stock['close']
            stocks = stocks.merge(temp_df, how='left', on='timestamp')
    stocks = stocks.fillna(method='ffill')
    stocks = stocks.fillna(method='backfill')
    return stocks

In [8]:
stocks_df = get_pandas_df(data)

In [9]:
stocks_df

timestamp  BARN.SW_close  E5H.SI_close  BN.VI_close   UN_close  \
0    2013-11-22         1018.0         0.585    38.892700  38.900002   
1    2013-11-25         1021.0         0.575    38.892700  39.340000   
2    2013-11-26         1028.0         0.585    38.892700  39.060001   
3    2013-11-27         1025.0         0.575    38.892700  39.090000   
4    2013-11-28         1031.0         0.575    38.892700  39.090000   
...         ...            ...           ...          ...        ...   
1748 2020-11-16         2026.0         0.146    54.700001  60.750000   
1749 2020-11-17         2000.0         0.153    54.419998  59.930000   
1750 2020-11-18         2016.0         0.152    54.619999  59.230000   
1751 2020-11-19         1988.0         0.148    52.880001  58.980000   
1752 2020-11-20         2006.0         0.150    53.500000  58.980000   

      LISN.SW_close   SJM_close  MDLZ_close  HRL_close  GIS_close   HSY_close  \
0           45850.0  103.949997   33.889999  21.450001  50.119999   96.290001   
1           45805.0  104.309998   33.610001  21.219999  49.880001   95.989998   
2           46300.0  105.620003   33.889999  22.475000  50.480000   96.919998   
3           46385.0  105.610001   33.980000  22.514999  50.529999   97.720001   
4           46695.0  105.610001   33.980000  22.514999  50.529999   97.720001   
...             ...         ...         ...        ...        ...         ...   
1748        84400.0  120.110001   58.680000  52.509998  61.209999  155.119995   
1749        83400.0  118.430000   58.540001  51.330002  61.279999  152.929993   
1750        85000.0  115.769997   57.759998  50.009998  61.130001  150.639999   
1751        84000.0  117.050003   57.599998  49.990002  62.000000  149.399994   
1752        83700.0  117.050003   57.599998  49.990002  62.000000  149.399994   

      KIKOY_close  WHG_close  ADM_close    K_close  NESN.SW_close  \
0         10.0567  56.820000  41.860001  62.470001      66.800003   
1         10.0567  56.750000  41.349998  62.130001      67.300003   
2         10.0567  56.880001  41.599998  61.730000      66.250000   
3         10.0567  57.000000  41.490002  60.880001      66.150002   
4         10.0567  57.000000  41.490002  60.880001      66.199997   
...           ...        ...        ...        ...            ...   
1748      24.7500  11.950000  50.410000  66.580002     105.080002   
1749      24.7500  12.650000  50.160000  66.320000     105.519997   
1750      24.7500  12.420000  49.270000  65.019997     104.959999   
1751      24.7500  12.400000  48.919998  65.209999     104.120003   
1752      24.7500  12.400000  48.919998  65.209999     103.820000   

      TATE.L_close   BG_close  ABF.L_close  CAG_close  
0       794.000000  80.720001       2291.0  25.431906  
1       798.500000  80.349998       2290.0  25.385214  
2       790.500000  80.650002       2250.0  25.252918  
3       787.000000  80.529999       2292.0  25.533073  
4       781.000000  80.529999       2290.0  25.533073  
...            ...        ...          ...        ...  
1748    678.200012  60.689999       2058.0  36.540001  
1749    673.400024  59.380001       2036.0  35.740002  
1750    674.000000  58.380001       2033.0  35.480000  
1751    645.599976  58.529999       1999.5  36.189999  
1752    651.599976  58.529999       1993.0  36.189999  

[1753 rows x 20 columns]

In [10]:
adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]

In [11]:
(adj_closes/adj_closes.iloc[0]*100).iplot()

In [12]:
# Mean daily return
returns = np.log(adj_closes/adj_closes.shift(1))
returns.mean()

BARN.SW_close    0.000387
E5H.SI_close    -0.000777
BN.VI_close      0.000182
UN_close         0.000238
LISN.SW_close    0.000344
SJM_close        0.000068
MDLZ_close       0.000303
HRL_close        0.000483
GIS_close        0.000121
HSY_close        0.000251
KIKOY_close      0.000514
WHG_close       -0.000869
ADM_close        0.000089
K_close          0.000025
NESN.SW_close    0.000252
TATE.L_close    -0.000113
BG_close        -0.000183
ABF.L_close     -0.000080
CAG_close        0.000201
dtype: float64

In [13]:
# Annual Returns
returns.mean() * 252

BARN.SW_close    0.097564
E5H.SI_close    -0.195757
BN.VI_close      0.045866
UN_close         0.059865
LISN.SW_close    0.086569
SJM_close        0.017072
MDLZ_close       0.076291
HRL_close        0.121699
GIS_close        0.030596
HSY_close        0.063182
KIKOY_close      0.129536
WHG_close       -0.218945
ADM_close        0.022418
K_close          0.006174
NESN.SW_close    0.063425
TATE.L_close    -0.028429
BG_close        -0.046236
ABF.L_close     -0.020043
CAG_close        0.050742
dtype: float64

In [14]:
# Annual covariance
returns.cov() * 252

BARN.SW_close  E5H.SI_close  BN.VI_close  UN_close  \
BARN.SW_close       0.042899      0.002761     0.007265  0.012810   
E5H.SI_close        0.002761      0.120149     0.001750  0.006384   
BN.VI_close         0.007265      0.001750     0.068809  0.010020   
UN_close            0.012810      0.006384     0.010020  0.044617   
LISN.SW_close       0.014723      0.003511     0.006687  0.013066   
SJM_close           0.007434      0.003107     0.006856  0.014540   
MDLZ_close          0.011245      0.005834     0.007833  0.022961   
HRL_close           0.006915      0.001126     0.005702  0.017290   
GIS_close           0.007627      0.003770     0.005589  0.015661   
HSY_close           0.008180      0.000376     0.006669  0.020336   
KIKOY_close         0.004027      0.008694     0.002468  0.006295   
WHG_close           0.009300      0.008413     0.007848  0.020728   
ADM_close           0.011042      0.009282     0.008400  0.021521   
K_close             0.006505      0.002742     0.005569  0.016284   
NESN.SW_close       0.015345      0.005688     0.009088  0.016175   
TATE.L_close        0.012948      0.008719     0.009139  0.015246   
BG_close            0.010490      0.007818     0.005953  0.019819   
ABF.L_close         0.016416      0.011344     0.011197  0.017854   
CAG_close           0.009092      0.002705     0.005822  0.015939   

               LISN.SW_close  SJM_close  MDLZ_close  HRL_close  GIS_close  \
BARN.SW_close       0.014723   0.007434    0.011245   0.006915   0.007627   
E5H.SI_close        0.003511   0.003107    0.005834   0.001126   0.003770   
BN.VI_close         0.006687   0.006856    0.007833   0.005702   0.005589   
UN_close            0.013066   0.014540    0.022961   0.017290   0.015661   
LISN.SW_close       0.033624   0.005369    0.011629   0.006010   0.006681   
SJM_close           0.005369   0.051524    0.024712   0.023716   0.029838   
MDLZ_close          0.011629   0.024712    0.050290   0.024637   0.026865   
HRL_close           0.006010   0.023716    0.024637   0.046039   0.025283   
GIS_close           0.006681   0.029838    0.026865   0.025283   0.044372   
HSY_close           0.010147   0.022890    0.029153   0.023843   0.025169   
KIKOY_close         0.007015   0.004308    0.010782   0.004836   0.005637   
WHG_close           0.019399   0.009297    0.030552   0.015683   0.015792   
ADM_close           0.011253   0.019121    0.030479   0.019578   0.020405   
K_close             0.004789   0.027043    0.026276   0.023877   0.031205   
NESN.SW_close       0.013695   0.008707    0.011303   0.007833   0.008464   
TATE.L_close        0.012910   0.008112    0.012163   0.007639   0.007530   
BG_close            0.012506   0.013466    0.024322   0.012855   0.014106   
ABF.L_close         0.017696   0.006547    0.013864   0.004240   0.007531   
CAG_close           0.006338   0.026075    0.025476   0.022735   0.026947   

               HSY_close  KIKOY_close  WHG_close  ADM_close   K_close  \
BARN.SW_close   0.008180     0.004027   0.009300   0.011042  0.006505   
E5H.SI_close    0.000376     0.008694   0.008413   0.009282  0.002742   
BN.VI_close     0.006669     0.002468   0.007848   0.008400  0.005569   
UN_close        0.020336     0.006295   0.020728   0.021521  0.016284   
LISN.SW_close   0.010147     0.007015   0.019399   0.011253  0.004789   
SJM_close       0.022890     0.004308   0.009297   0.019121  0.027043   
MDLZ_close      0.029153     0.010782   0.030552   0.030479  0.026276   
HRL_close       0.023843     0.004836   0.015683   0.019578  0.023877   
GIS_close       0.025169     0.005637   0.015792   0.020405  0.031205   
HSY_close       0.051451     0.008982   0.035421   0.023597  0.023286   
KIKOY_close     0.008982     0.118612   0.017798   0.007767  0.004539   
WHG_close       0.035421     0.017798   0.192617   0.041177  0.011923   
ADM_close       0.023597     0.007767   0.041177   0.064850  0.021713   
K_close         0.023286     0.004539   0.011923   0.021713  0.046090  

In [15]:
returns.corr().iplot(kind='heatmap',colorscale="Blues", title="Stocks Correlation Matrix")

In [16]:
num_assets = len(returns.columns)
weights = np.random.dirichlet(np.ones(num_assets), size=1)
weights = weights[0]
print(weights)
print(f"Number of weights: {len(weights)}")
print(f"Sum of weights: {np.sum(weights)}")

[0.07652884 0.00121641 0.05629184 0.00150295 0.09721645 0.01115116
 0.02806322 0.0703438  0.07909852 0.004994   0.09647271 0.30033263
 0.03186003 0.00102622 0.0431078  0.08910013 0.00215978 0.00250003
 0.00703351]
Number of weights: 19
Sum of weights: 0.9999999999999999


In [17]:
# EXPECTED PORTFOLIO RETURN:
exp_port_return = np.sum(returns.mean()*weights)*252
print(exp_port_return)

-0.020187304059394517


In [18]:
# VARAICNE AND VOLATILITY
port_var = np.dot(weights.T, np.dot(returns.cov()*252, weights))
port_vol = np.sqrt(port_var)
print(port_var)
print(port_vol)

0.03210199863278612
0.17917030622507213


In [28]:
import time

import plotly.graph_objects as go
import numpy as np

def portfolio_simulation(assets, iterations):
    '''
    Runs a simulation by randomly selecting portfolio weights a specified
    number of times (iterations), returns the list of results and plots 
    all the portfolios as well.
    
    Parameters:
    -----------  
        assets: list
            all the assets that are to be pulled from Quandl to comprise
            our portfolio.    
        iterations: int 
            the number of randomly generated portfolios to build.
    
    Returns:
    --------
        port_returns: array
            array of all the simulated portfolio returns.
        port_vols: array
            array of all the simulated portfolio volatilities.
    '''
    
    start = time.time()
    num_assets = len(assets)
    
    # Fetch data 
    data = fetch_data(ticker_list, verbose=False)
    stocks = get_pandas_df(data)
    adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]

    returns = np.log(adj_closes / adj_closes.shift(1))
    
    port_returns = []
    port_vols = []
    
    for i in range (iterations):
        weights = np.random.dirichlet(np.ones(num_assets),size=1)
        weights = weights[0]
        port_returns.append(np.sum(returns.mean() * weights) * 252)
        port_vols.append(np.sqrt(np.dot(weights.T, np.dot(returns.cov() * 252, weights))))
    
    # Convert lists to arrays
    port_returns = np.array(port_returns)
    port_vols = np.array(port_vols)
    len_ret = port_returns.shape[0]
    portfolio_stats = pd.DataFrame()
    portfolio_stats['returns'] = port_returns
    portfolio_stats['vol'] = port_vols
    portfolio_stats = portfolio_stats.sort_values(by='returns', ascending=False)
    portfolio_stats = portfolio_stats.loc[portfolio_stats.returns>=0]
    portfolio_stats = portfolio_stats.iloc[list(range(0,portfolio_stats.shape[0],5)),:]
    
    fig = go.Figure(data=go.Scatter(x=portfolio_stats.vol,
                                    y=portfolio_stats.returns, mode='markers',
                                   marker=dict(
        size=5,
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=True)))

    fig.show()
    
    print('Elapsed Time: %.2f seconds' % (time.time() - start))
    
    return port_returns, port_vols

In [29]:
port_returns, port_vols = portfolio_simulation(ticker_list, 30000)

Elapsed Time: 62.51 seconds


In [37]:
data = fetch_data(ticker_list, verbose=False)
stocks = get_pandas_df(data)
adj_closes = stocks_df[[x for x in stocks.columns if x !='timestamp']]
returns = np.log(adj_closes / adj_closes.shift(1))

def portfolio_stats(weights):
    # Convert to array in case list was passed instead.
    weights = np.array(weights)
    
    port_return = np.sum(returns.mean() * weights) * 252
    port_vol = np.sqrt(np.dot(weights.T, np.dot(returns.cov() * 252, weights)))
    sharpe = port_return/port_vol

    return {'return': port_return, 'volatility': port_vol, 'sharpe': sharpe}

def minimize_sharpe(weights):  
    return -portfolio_stats(weights)['sharpe'] 

def minimize_volatility(weights):  
    # Note that we don't return the negative of volatility here because we 
    # want the absolute value of volatility to shrink, unlike sharpe.
    return portfolio_stats(weights)['volatility'] 

def minimize_return(weights): 
    return -portfolio_stats(weights)['return']

In [46]:
constraints = ({'type' : 'eq', 'fun': lambda x: np.sum(x) -1})
bounds = tuple((0,1) for x in range(num_assets))
initializer = num_assets * [1./num_assets,]

## Efficient frontier - optimal sharpe ration

In [32]:
import scipy.optimize as optimize
optimal_sharpe = optimize.minimize(minimize_sharpe,
                                  initializer,
                                  method = 'SLSQP',
                                  bounds = bounds,
                                  constraints = constraints)
print(optimal_sharpe)

     fun: -0.7958907710956635
     jac: array([-2.58333981e-04,  1.59993501e+00, -6.22421503e-04,  1.48655236e-01,
        1.52982771e-04,  4.19608712e-01,  1.39162160e-01,  3.12641263e-04,
        3.66279893e-01,  1.64831966e-01, -4.87759709e-04,  2.30204212e+00,
        4.34750482e-01,  4.87746373e-01, -6.48200512e-05,  6.72623798e-01,
        8.44022371e-01,  6.50443986e-01,  2.07740255e-01])
 message: 'Optimization terminated successfully.'
    nfev: 189
     nit: 9
    njev: 9
  status: 0
 success: True
       x: array([2.25161889e-01, 0.00000000e+00, 3.01605456e-02, 0.00000000e+00,
       2.33270258e-01, 2.57240518e-16, 0.00000000e+00, 3.61989055e-01,
       0.00000000e+00, 3.74503759e-16, 1.47096895e-01, 6.76670905e-16,
       0.00000000e+00, 1.39401294e-16, 2.32135793e-03, 7.52775121e-17,
       0.00000000e+00, 2.08282014e-16, 9.84116759e-17])


In [33]:
optimal_sharpe_weights=optimal_sharpe['x'].round(4)
list(zip(ticker_list,list(optimal_sharpe_weights)))

[('BARN.SW', 0.2252),
 ('E5H.SI', 0.0),
 ('BN.VI', 0.0302),
 ('UN', 0.0),
 ('LISN.SW', 0.2333),
 ('SJM', 0.0),
 ('MDLZ', 0.0),
 ('HRL', 0.362),
 ('GIS', 0.0),
 ('HSY', 0.0),
 ('KIKOY', 0.1471),
 ('WHG', 0.0),
 ('ADM', 0.0),
 ('K', 0.0),
 ('NESN.SW', 0.0023),
 ('TATE.L', 0.0),
 ('BG', 0.0),
 ('ABF.L', 0.0),
 ('CAG', 0.0)]

## Efficient frontier - optimal variance

In [34]:
optimal_variance=optimize.minimize(minimize_volatility,
                                   initializer,
                                   method = 'SLSQP',
                                   bounds = bounds,
                                   constraints = constraints)

print(optimal_variance)
optimal_variance_weights=optimal_variance['x'].round(4)
list(zip(ticker_list,list(optimal_variance_weights)))

     fun: 0.11333664458580414
     jac: array([0.11308901, 0.11324737, 0.11377023, 0.11934087, 0.11337896,
       0.11328077, 0.12943432, 0.11332569, 0.11341272, 0.11322731,
       0.11326975, 0.12101097, 0.12087961, 0.11329019, 0.11323559,
       0.11356294, 0.11325792, 0.11336607, 0.11341738])
 message: 'Optimization terminated successfully.'
    nfev: 231
     nit: 11
    njev: 11
  status: 0
 success: True
       x: array([8.97204012e-02, 7.63141779e-02, 1.04331761e-01, 0.00000000e+00,
       1.56719945e-01, 4.36171131e-02, 4.11996826e-18, 8.80167455e-02,
       1.63533765e-02, 1.82840487e-02, 6.27167017e-02, 3.52365706e-19,
       4.24871726e-18, 8.69403909e-02, 1.83084577e-01, 3.97274815e-02,
       2.31512673e-02, 2.71050543e-20, 1.10220126e-02])


[('BARN.SW', 0.0897),
 ('E5H.SI', 0.0763),
 ('BN.VI', 0.1043),
 ('UN', 0.0),
 ('LISN.SW', 0.1567),
 ('SJM', 0.0436),
 ('MDLZ', 0.0),
 ('HRL', 0.088),
 ('GIS', 0.0164),
 ('HSY', 0.0183),
 ('KIKOY', 0.0627),
 ('WHG', 0.0),
 ('ADM', 0.0),
 ('K', 0.0869),
 ('NESN.SW', 0.1831),
 ('TATE.L', 0.0397),
 ('BG', 0.0232),
 ('ABF.L', 0.0),
 ('CAG', 0.011)]

In [41]:
# Make an array of 50 returns betweeb the minimum return and maximum return
# discovered earlier.
target_returns = np.linspace(0,0.12,100)

# Initialize optimization parameters
minimal_volatilities = []
bounds = tuple((0,1) for x in weights)
initializer = num_assets * [1./num_assets,]

for target_return in target_returns:
    
    constraints = ({'type':'eq','fun': lambda x: portfolio_stats(x)['return']-target_return},
                   {'type':'eq','fun': lambda x: np.sum(x)-1})
       
    optimal = optimize.minimize(minimize_volatility,
                              initializer,
                              method = 'SLSQP',
                              bounds = bounds,

                                constraints = constraints)
    
    minimal_volatilities.append(optimal['fun'])

minimal_volatilities = np.array(minimal_volatilities)

In [45]:
port_returns = np.array(port_returns)
port_vols = np.array(port_vols)
len_ret = port_returns.shape[0]
portfolio_stats1 = pd.DataFrame()
portfolio_stats1['returns'] = port_returns
portfolio_stats1['vol'] = port_vols
portfolio_stats1 = portfolio_stats1.sort_values(by='returns', ascending=False)
portfolio_stats1 = portfolio_stats1.loc[portfolio_stats1.returns>=0]
portfolio_stats1 = portfolio_stats1.iloc[list(range(0,portfolio_stats1.shape[0],5)),:]

fig = go.Figure()
fig.add_trace(go.Scatter(x=portfolio_stats1.vol,
                         y=portfolio_stats1.returns, mode='markers',
                         marker=dict(
        size=5,
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=False)))

fig.add_trace(go.Scatter(x=minimal_volatilities, y=target_returns, mode='markers',
                                   marker=dict(
        size=5,
        symbol='diamond',
        color=(port_returns / port_vols), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=True)))

fig.add_trace(go.Scatter(x=[portfolio_stats(optimal_sharpe_weights)['volatility']],
                         y=[portfolio_stats(optimal_sharpe_weights)['return']],
                         mode='markers',
                                   marker=dict(
        size=15,
        color='red',
        symbol='triangle-up',
        showscale=True)))

fig.show()